# Tree-sitter

```{note}
[Tree-sitter](https://tree-sitter.github.io/tree-sitter/index.html) 是一个跨语言的语法解析器生成工具，支持 C++、Python、Java 等多种语言。它的特点是：
1. 能为代码构建抽象语法树（AST），即使代码存在语法错误，也会尝试生成尽可能完整的树，并标记错误位置。
2. 提供 API 供开发者遍历语法树，检查节点类型（包括 “错误节点”）。
```

## 使用 Tree-sitter 检测代码中的语法错误

以使用 Python 绑定库，检测 C++ 代码为例子。核心思路是<span style="color: red">利用其解析能力生成语法树，再通过检查语法树中是否存在 “错误节点” 来判断代码是否有语法问题。</span>

### Install

```bash
# 安装 Python 绑定
pip install tree-sitter
```

```bash
# 安装 C++ 语言预编译包
pip install tree-sitter-cpp
```

## Example

In [1]:
from tree_sitter import Parser, Language
import tree_sitter_cpp as tscpp


def has_cpp_syntax_errors(code: str) -> bool:
    """检查 C++ 代码是否存在语法错误（基于 tree-sitter-cpp 预编译包）"""
    # 1. 初始化解析器并加载 C++ 语言定义（无需手动编译）
    CPP_LANGUAGE = Language(tscpp.language())
    parser = Parser(CPP_LANGUAGE)

    # 2. 解析代码生成语法树
    tree = parser.parse(code.encode("utf-8"))
    root_node = tree.root_node

    # 3. 遍历语法树，检查是否有 ERROR 节点
    def traverse(node):
        if node.type == "ERROR":
            return True
        for child in node.children:
            if traverse(child):
                return True
        return False

    return traverse(root_node)


# 有语法错误的 C++ 代码（括号不匹配）
bad_code = """
#include <iostream>
int main() {
    std::cout << "Hello World" << std::endl
    // 缺少分号 }
"""

# 无语法错误的 C++ 代码
good_code = """
#include <iostream>
int main() {
    std::cout << "Hello World" << std::endl;
    return 0;
}
"""

print("Bad code has errors:", has_cpp_syntax_errors(bad_code))  # 输出 True
print("Good code has errors:", has_cpp_syntax_errors(good_code))  # 输出 False

Bad code has errors: True
Good code has errors: False
